# Iteration 5: FPV Weight

In [1]:
from unyt import km, m, mm, inch, g, kg, hr, minute, s, degree, radian, volt
import numpy as np
from matplotlib import pyplot as plt
from math import pi as π
%matplotlib inline

In [2]:
rpm = minute**-1

In [3]:
ρ = 1.225*kg/m**3 # air density
μinf = 1.81e-5*kg/(m*s) # viscosity of air

Goals:
- Use more accurate weight estimate with FPV system

## Initial Design

In [4]:
b = 3050*mm # wingspan
c = 230*mm # chord

In [5]:
S = b*c # wing area
AR = b**2/S

In [6]:
AR

unyt_quantity(13.26086957, '(dimensionless)')

## Weight Estimate

Weight estimate decreased from 3047 to 3000 (included real FPV system weight, more realistic telem weight, increased payload from 500g to 700g).

In [7]:
W = 3000*g # weight

|Part                 |Volume     |Fraction solid|Weight |Area|Count|Weight total|
|---------------------|-----------|--------------|-------|----|-----|------------|
|Wing                 |6.42188e+06|0.3           |257.793|    |2    |515.585     |
|Fuselage             |54465.1    |1             |7.08046|    |1    |7.08046     |
|Tail boom            |353429     |1             |197.92 |    |1    |197.92      |
|Wing spar            |120000     |1             |63.4921|    |2    |126.984     |
|Horizontal stabilizer|140000     |1             |15.08  |    |1    |15.08       |
|Vertical stabilizer  |37500      |1             |4.03929|    |1    |4.03929     |
|Stabilizer mount     |51465.8    |1             |6.69056|    |1    |6.69056     |
|Battery              |           |              |604.8  |    |1    |604.8       |
|ESC                  |           |              |70     |    |1    |70          |
|Motor                |           |              |300    |    |1    |300         |
|Prop                 |           |              |87     |    |1    |87          |
|Pixhawk              |           |              |38     |    |1    |38          |
|GPS                  |           |              |30     |    |1    |30          |
|Telem                |           |              |40     |    |1    |40          |
|Servo                |           |              |35     |    |4    |140         |
|GoPro                |           |              |       |    |     |74          |
|FPV OSD              |           |              |3      |    |1    |3           |
|FPV VTX              |           |              |6      |    |1    |6           |
|Power distribution   |           |              |       |    |     |30          |
|Payload              |           |              |       |    |     |700         |
|Total                |           |              |       |    |     |2996.18     |

## Airfoil Selection

In [8]:
V = 30*km/hr # cruise speed

In [9]:
CL = (2*W)/(ρ*V**2*S)
print(f"CL: {CL.to_value('s**2/m')}")

CL: 0.1005425691302893


In [10]:
(V**2)

unyt_quantity(900, 'km**2/hr**2')

In [11]:
Re = (ρ*V*c)/μinf
round(Re.to_value(), -3)

130000.0

In [12]:
α0 = -3.75*degree
Clα = 1.05
e = 0.8

In [13]:
CLα = Clα/(1+(Clα/(π*e*AR)))

In [14]:
CL_unitless = CL.to_value('s**2/m')

In [15]:
α = α0+((CL_unitless/CLα)*radian)
α

unyt_quantity(1.90919406, 'degree')

In [16]:
CLmax = 1.4*s**2/m
Vstall = np.sqrt((2*W)/(ρ*S*CLmax))
print(f"Cruise speed: {V.to('m/s'):.2f}, Stall speed: {Vstall:.2f}")

Cruise speed: 8.33 m/s, Stall speed: 2.23 m/s


## Wing Loading and Thrust to Weight Ratio

In [17]:
WCL = W/(S**(3/2))
print(f"Wing loading: {WCL.to('kg/m**3'):.2f}")

Wing loading: 5.11 kg/m**3


In [18]:
TtoW = 1.1
T = TtoW*W
print(f"Required thrust: {T.to('kg'):.2f}")

Required thrust: 3.30 kg


## Propulsion System

The propulsion system selection is identical to iteration 4 (16x10/500Kv/6S), because the weight has only been slightly adjusted.

## FPV System

I'll be using Holybro's [`Micro OSD V2`](https://shop.holybro.com/micro-osd-v2_p1207.html) + [`Atlatl HV micro`](https://shop.holybro.com/atlatl-hv-micro_p1186.html). The former uses 5V power from the telemetry port and the latter can run off of the 6S pack.

Hobbyking currently has an excellent offer (€26.09) on the [`Quanum Cyclops Diversity DVR FPV Goggle`](https://hobbyking.com/en_us/quanum-cyclops-diversity-fpv-goggle.html), which as the name suggests are a single-screen model with build-in DVR. They are 5.8GHz 40CH, like the `Atlatl HV micro` VTX.

## Servos

By using [Radio Control Info's Servo Torque Calculator](https://www.radiocontrolinfo.com/information/rc-calculators/rc-airplane-calculator/#Torque) I calculated that I need servos with at least 5kg of torque for the ailerons. 

I decided to go with four of the [`HXT12K Metal Gear Servo 25T 11kg / 0.16sec / 55g `](https://hobbyking.com/en_us/hxt-10kg-servo-metal-gear-10kg-0-16sec-55g.html) (two in the wing for the aelerons and two in the fuselage for the elevator + rudder). They produce ample torque for all control surfaces.

I did consider the [`Turnigy TGY-813 Slim Wing DS/MG Servo 25T 9.0kg / 0.09sec / 30g`](https://hobbyking.com/en_us/turnigy-tgy-813-slim-wing-ds-mg-servo.html?queryID=&objectID=74683&indexName=hbk_live_magento_en_us_products_hbk_price_stock_7_group_0_asc), which are quite a bit lighter and of course more low profile. However, the HXT12K's fit in the wing anyway, and my wrong weight estimate of 140g vs the actual 220g will not make *that* big of a difference. There were not that many other options outside of these two categories, at least not with 3+kg torque. 

## Radio

I went with the incredibly simple [`Turnigy TGY-i4X Mode 2 AFHDS/AFHDS 2A Switchable 4CH Transmitter/Receiver `](https://hobbyking.com/en_us/turnigy-tgy-i4x-mode-2-afhds-afhds-2a-switchable-4ch-transmitter-receiver.html). It has no special qualifications except for having 4 channels and being the cheapest option. On the receiving end I'll be using the [`FS-A8S 2.4Ghz 8CH Mini Receiver with PPM i-BUS SBUS Output`](https://hobbyking.com/en_us/fs-a8s-2-4g-8ch-mini-receiver-with-ppm-i-bus-sbus-output.html) for SBus output.

I was considering using a completely digital system (using the 2-way telemetry connection for control) as I do plan on flying autonomously for the most part, but decided against it for safety/redundancy reasons.

## BOM

Also available as [iteration_5-bom-and-receipt](iteration_5-bom-and-receipt).

|Part             |Name                                                                                |Store    |Link                                                                                                              |Price pp|#  |Price total|
|-----------------|------------------------------------------------------------------------------------|---------|------------------------------------------------------------------------------------------------------------------|--------|---|-----------|
|Flight controller|Pixhawk 2.4.8                                                                       |second hand|https://www.2dehands.be/a/hobby-en-vrije-tijd/modelbouw-radiografisch-helikopters-en-quadcopters/m1658504570-pixhawk-2-4-8-px4-32bit-apm-flight-controller-with-power-mod.html?previousPage=lr|40      |1  |40         |
|Servo            |HXT12K Metal Gear Servo 25T 11kg / 0.16sec / 55g                                    |HobbyKing|https://hobbyking.com/en_us/hxt-10kg-servo-metal-gear-10kg-0-16sec-55g.html                                       |8.88    |4  |35.52      |
|Control horns    |Control Horns 16x20mm (10pcs)                                                       |HobbyKing|https://hobbyking.com/en_us/control-horns-16x20mm-10pcs.html                                                      |1.22    |1  |1.22       |
|Linkage holders  |Nylon Arm 2.8 x 6 x 6mm (10pcs)                                                     |HobbyKing|https://hobbyking.com/en_us/nylon-arm-2-8-x-6-x-6mm-10pcs.html                                                    |0.48    |1  |0.48       |
|Motor            |PROPDRIVE v2 4258 500KV Brushless Outrunner Motor                                   |HobbyKing|https://hobbyking.com/en_us/propdrive-v2-4258-500kv-brushless-outrunner-motor.html                                |46.1    |1  |46.1       |
|Prop             |TGS Precision Sport Propeller 17x10                                                 |HobbyKing|https://hobbyking.com/en_us/tgs-precision-sport-propeller-17x10-1pc.html                                          |6.14    |3  |18.42      |
|ESC              |YEP 80A (2~6S) SBEC                                                                 |HobbyKing|https://hobbyking.com/en_us/yep-80a-2-6s-sbec-brushless-speed-controller.html                                     |43.49   |1  |43.49      |
|ESC programmer   |YEP ESC Programming Card                                                            |HobbyKing|https://hobbyking.com/en_us/yep-esc-programming-card.html                                                         |5.92    |1  |5.92       |
|Battery          |Turnigy nano-tech 4000mAh 6S 35~70C                                                 |HobbyKing|https://hobbyking.com/en_us/turnigy-nano-tech-4000mah-6s-35-70c-lipo-pack-w-xt-90.html                            |63.39   |1  |63.39      |
|Radio transmitter|Turnigy TGY-i4X Mode 2 AFHDS/AFHDS 2A Switchable 4CH Transmitter/Receiver           |HobbyKing|https://hobbyking.com/en_us/turnigy-tgy-i4x-mode-2-afhds-afhds-2a-switchable-4ch-transmitter-receiver.html        |31.49   |1  |31.49      |
|Radio receiver   |FS-A8S 2.4Ghz 8CH Mini Receiver with PPM i-BUS SBUS Output                          |HobbyKing|https://hobbyking.com/en_us/fs-a8s-2-4g-8ch-mini-receiver-with-ppm-i-bus-sbus-output.html                         |7.59    |1  |7.59       |
|FPV goggles      |Quanum Cyclops Diversity DVR FPV Goggle                                             |HobbyKing|https://hobbyking.com/en_us/quanum-cyclops-diversity-fpv-goggle.html                                              |26.09   |1  |26.09      |
|FPV Cam          |CADDX Baby Ratel Starlight 1.8mm 1200TVL 14x14mm 4.6g FPV Camera w/160° FOV (Yellow)|HobbyKing|https://hobbyking.com/en_us/caddx-baby-ratel-starlight-1-8mm-1200tvl-14x14mm-4-6g-fpv-camera-w-160-fov-yellow.html|25.51   |1  |25.51      |
|FPV OSD          |Micro OSD V2                                                                        |Holybro  |https://shop.holybro.com/micro-osd-v2_p1207.html                                                                  |13.17   |1  |13.17      |
|FPV VTX          |Atlatl HV micro                                                                     |Holybro  |https://shop.holybro.com/atlatl-hv-micro_p1186.html                                                               |17.29   |1  |17.29      |
|Telemetry        |Transceiver Telemetry Radio V3                                                      |Holybro  |https://shop.holybro.com/transceiver-telemetry-radio-v3_p1103.html                                                |37.05   |1  |37.05      |
|GPS              |Pixhawk4 2nd GPS Module                                                             |Holybro  |https://shop.holybro.com/pixhawk4-2nd-gps-module_p1145.html                                                       |34.58   |1  |34.58      |
|Charger          |Turnigy P606 LiPoly/LiFe AC/DC Charger (EU Plug)                                    |HobbyKing|https://hobbyking.com/en_us/pd606-charger-eu-plug.html                                                            |43.15   |1  |43.15      |
|                 |                                                                                    |         |                                                                                                                  |        |   |           |
|Total            |                                                                                    |         |                                                                                                                  |        |   |490.46     |


## Receipt
|Name             |Link                                                                                |Price w/o fees|Paid                                                                                                              |Fees (shipping/conversion/handling/service…)|
|-----------------|------------------------------------------------------------------------------------|--------------|------------------------------------------------------------------------------------------------------------------|--------------------------------------------|
|Second hand: Flight controller|https://www.2dehands.be/a/hobby-en-vrije-tijd/modelbouw-radiografisch-helikopters-en-quadcopters/m1658504570-pixhawk-2-4-8-px4-32bit-apm-flight-controller-with-power-mod.html?previousPage=lr|40            |40                                                                                                                |0                                           |
|HobbyKing        |https://hobbyking.com/                                                              |348.37        |397.59                                                                                                            |49.22                                       |
|Holybro          |https://shop.holybro.com/                                                           |102.09        |147.84                                                                                                            |45.75                                       |
|                 |                                                                                    |              |                                                                                                                  |                                            |
|Total            |                                                                                    |              |585.43                                                                                                            |94.97                                       |
